# Transforming Unstructured Data from an AWS S3 bucket into RAG-Ready Data in Singdata Lakehouse

In [1]:
import json
import pandas as pd
import logging
import warnings

logging.basicConfig(level=logging.ERROR, force=True)
warnings.filterwarnings("ignore", category=UserWarning)

# if you want to drop the tables before write data, set drop_tables to True
drop_tables = True

In [2]:
import os
import dotenv

dotenv.load_dotenv('./.env') # replace with the path to your .env file

True

In [3]:
# Define the table names to use for storing the data in Lakehouse.
# index_and_table_prefix = "base_512_"
# raw_table_name = f"{index_and_table_prefix}yunqi_raw_elements"
# silver_table_name = f"{index_and_table_prefix}yunqi_elements"
# embeddings_dimensions = 768
# chunk_max_characters =512
# chunk_overlap = 200
# embedding_provider = "huggingface"
# embedding_model_name = "BAAI/bge-base-zh-v1.5"


index_and_table_prefix = "m3_1024_2048_"
raw_table_name = f"{index_and_table_prefix}yunqi_raw_elements"
silver_table_name = f"{index_and_table_prefix}yunqi_elements"
embeddings_dimensions = 1024
chunk_max_characters =2048
chunk_overlap = 512
embedding_provider = "huggingface"
embedding_model_name = "BAAI/bge-m3"


In [4]:
# Get the connection parameter to Singdata Lakehouse.
_username = os.getenv("cz_username")
_password = os.getenv("cz_password")
_service = os.getenv("cz_service")
_instance = os.getenv("cz_instance")
_workspace = os.getenv("cz_workspace")
_schema = os.getenv("cz_schema")
_vcluster = os.getenv("cz_vcluster")

In [5]:
# Define the schema to use for storing the data in Singdata Lakehouse.
raw_table_ddl = f"""
CREATE TABLE IF NOT EXISTS {_schema}.{raw_table_name} (
    id STRING, -- Auto-increment sequence
    record_locator STRING,
    type STRING,
    record_id STRING, -- Record identifier from the data source (e.g., record locator in connector metadata)
    element_id STRING, -- Unique identifier for the element (SHA-256 or UUID)
    filetype STRING, -- File type (e.g., PDF, DOCX, EML, etc.)
    file_directory STRING, -- Directory where the file is located
    filename STRING, -- File name
    last_modified TIMESTAMP, -- Last modified time of the file
    languages STRING, -- Document language, supports a list of multiple languages
    page_number STRING, -- Page number (applicable for PDF, DOCX, etc.)
    text STRING, -- Extracted text content
    embeddings VECTOR({embeddings_dimensions}), -- Vector data
    parent_id STRING, -- Parent element ID, used to represent element hierarchy
    is_continuation BOOLEAN, -- Whether it is a continuation of the previous element (used in chunking)
    orig_elements STRING, -- Original element in JSON format (used to store the complete element structure)
    element_type STRING, -- Element type (e.g., NarrativeText, Title, Table, etc.)
    coordinates STRING, -- Element coordinates (stored in JSONB format)
    link_texts STRING, -- Added field: Link text
    link_urls STRING, -- Added field: Link URL
    email_message_id STRING, -- Added field: Email message ID
    sent_from STRING, -- Added field: Sender
    sent_to STRING, -- Added field: Recipient
    subject STRING, -- Added field: Subject
    url STRING, -- Added field: URL
    version STRING, -- Added field: Version
    date_created TIMESTAMP, -- Added field: Creation date
    date_modified TIMESTAMP, -- Added field: Modification date
    date_processed TIMESTAMP, -- Added field: Processing date
    text_as_html STRING, -- Added field: Text in HTML format
    emphasized_text_contents STRING,
    emphasized_text_tags STRING,
    documents_original_source STRING, -- Added field: Document source
);
"""

silver_table_ddl = f"""
CREATE TABLE IF NOT EXISTS {_schema}.{silver_table_name} (
    id STRING, -- Auto-increment sequence
    record_locator STRING,
    type STRING,
    record_id STRING, -- Record identifier from the data source (e.g., record locator in connector metadata)
    element_id STRING, -- Unique identifier for the element (SHA-256 or UUID)
    filetype STRING, -- File type (e.g., PDF, DOCX, EML, etc.)
    file_directory STRING, -- Directory where the file is located
    filename STRING, -- File name
    last_modified TIMESTAMP, -- Last modified time of the file
    languages STRING, -- Document language, supports a list of multiple languages
    page_number STRING, -- Page number (applicable for PDF, DOCX, etc.)
    text STRING, -- Extracted text content
    embeddings vector({embeddings_dimensions}), -- Vector data
    parent_id STRING, -- Parent element ID, used to represent element hierarchy
    is_continuation BOOLEAN, -- Whether it is a continuation of the previous element (used in chunking)
    orig_elements STRING, -- Original element in JSON format (used to store the complete element structure)
    element_type STRING, -- Element type (e.g., NarrativeText, Title, Table, etc.)
    coordinates STRING, -- Element coordinates (stored in JSONB format)
    link_texts STRING, -- Added field: Link text
    link_urls STRING, -- Added field: Link URL
    email_message_id STRING, -- Added field: Email message ID
    sent_from STRING, -- Added field: Sender
    sent_to STRING, -- Added field: Recipient
    subject STRING, -- Added field: Subject
    url STRING, -- Added field: URL
    version STRING, -- Added field: Version
    date_created TIMESTAMP, -- Added field: Creation date
    date_modified TIMESTAMP, -- Added field: Modification date
    date_processed TIMESTAMP, -- Added field: Processing date
    text_as_html STRING, -- Added field: Text in HTML format
    emphasized_text_contents STRING,
    emphasized_text_tags STRING,
    documents_source STRING, -- Added field: Document source
    INDEX {index_and_table_prefix}inverted_text_index_yunqi_cn (text) INVERTED  PROPERTIES('analyzer'='unicode'),
    INDEX {index_and_table_prefix}embeddings_vec_index_yunqi_cn(embeddings) USING vector properties (
        "scalar.type" = "f32",
        "distance.function" = "cosine_distance")
);
"""

clean_transformation_data_sql = f"""
INSERT overwrite {_schema}.{silver_table_name}
SELECT 
    id, 
    record_locator, 
    type, 
    record_id, 
    element_id, 
    filetype, 
    file_directory, 
    filename, 
    last_modified, 
    languages, 
    page_number, 
    text, 
    CAST(embeddings AS VECTOR({embeddings_dimensions})) AS embeddings, 
    parent_id, 
    is_continuation, 
    orig_elements, 
    element_type, 
    coordinates, 
    link_texts, 
    link_urls, 
    email_message_id, 
    sent_from, 
    sent_to, 
    subject, 
    url, 
    version, 
    date_created, 
    date_modified, 
    date_processed, 
    text_as_html,
    emphasized_text_contents, 
    emphasized_text_tags,
    "https://yunqi.tech/documents" as documents_source
FROM {_schema}.{raw_table_name};
"""

In [6]:
# Define the function to create the connection to Singdata Lakehouse.
from clickzetta.connector import connect
import pandas as pd
def get_connection(password, username, service, instance, workspace, schema, vcluster):
    connection = connect(
        password=password,
        username=username,
        service=service,
        instance=instance,
        workspace=workspace,
        schema=schema,
        vcluster=vcluster)
    return connection

In [7]:
# Create the connection to Singdata Lakehouse.
conn = get_connection(password=_password, username=_username, service=_service, instance=_instance, workspace=_workspace, schema=_schema, vcluster=_vcluster)

In [8]:
# Function to execute SQL statements
def excute_sql(conn,sql_statement: str):
    with conn.cursor() as cur:

        stmt = sql_statement

        cur.execute(stmt)

        results = cur.fetchall()

    return results

In [9]:
if drop_tables:
    excute_sql(conn,f"DROP TABLE IF EXISTS {_schema}.{raw_table_name}")
    # excute_sql(conn,f"DROP TABLE IF EXISTS {_schema}.{silver_table_name}")

In [10]:
# Create Table in Singdata Lakehouse
excute_sql(conn, raw_table_ddl)
excute_sql(conn, silver_table_ddl)

[['OPERATION SUCCEED']]

### PDFs/Images/Emails ingestion and preprocessing pipeline

In [11]:
from unstructured_ingest.interfaces import ProcessorConfig
from unstructured_ingest.pipeline.pipeline import Pipeline
from unstructured_ingest.processes.chunker import ChunkerConfig
from unstructured_ingest.processes.connectors.fsspec.s3 import (
    S3ConnectionConfig,
    S3DownloaderConfig,
    S3IndexerConfig,
    S3AccessConfig,
)
from unstructured_ingest.processes.connectors.local import (
    LocalIndexerConfig,
    LocalDownloaderConfig,
    LocalConnectionConfig
)
from unstructured_ingest.processes.embedder import EmbedderConfig
from unstructured_ingest.processes.partitioner import PartitionerConfig

from unstructured_ingest.processes.connectors.sql.clickzetta import (
    ClickzettaConnectionConfig,
    ClickzettaAccessConfig,
    ClickzettaUploadStagerConfig,
    ClickzettaUploaderConfig
)

In [12]:
# !rm -rf /Users/liangmo/.cache/unstructured/ingest/pipeline/*

In [13]:
os.getenv("LOCAL_FILE_INPUT_DIR")

'/Users/liangmo/yunqidoc/cn_markdown_20250526'

In [14]:
pipeline = Pipeline.from_configs(

    context=ProcessorConfig(
        verbose=True,
        tqdm=True,
        num_processes=8,
    ),

    indexer_config=LocalIndexerConfig(input_path=os.getenv("LOCAL_FILE_INPUT_DIR"),file_glob="**/*", recursive=True),
        downloader_config=LocalDownloaderConfig(),
        source_connection_config=LocalConnectionConfig(),

    partitioner_config=PartitionerConfig(
        partition_by_api=False,
        api_key=os.getenv("UNSTRUCTURED_API_KEY"),
        partition_endpoint=os.getenv("UNSTRUCTURED_URL"),
        strategy="hi_res",
        additional_partition_args={
            "split_pdf_page": True,
            "split_pdf_allow_failed": True,
            "split_pdf_concurrency_level": 8
        }
    ),

    chunker_config=ChunkerConfig(
        chunking_strategy="by_title",
        chunk_max_characters=chunk_max_characters,
        chunk_overlap=chunk_overlap,
        chunk_combine_text_under_n_chars=200,
    ),

    embedder_config=EmbedderConfig(
        embedding_provider = embedding_provider,
        embedding_model_name = embedding_model_name,
    ),

    destination_connection_config=ClickzettaConnectionConfig(
        access_config=ClickzettaAccessConfig(password=_password),
        username=_username,
        service=_service,
        instance=_instance,
        workspace=_workspace,
        schema=_schema,
        vcluster=_vcluster,
    ),
    stager_config=ClickzettaUploadStagerConfig(),
    uploader_config=ClickzettaUploaderConfig(table_name=raw_table_name, documents_original_source="https://yunqi.tech/documents"),
)

pipeline.run()

2025-05-26 19:23:12,626 MainProcess INFO     created indexer with configs: {"input_path":"/Users/liangmo/yunqidoc/cn_markdown_20250526","recursive":true}, connection configs: {"access_config":"**********"}
2025-05-26 19:23:12,627 MainProcess INFO     Created download with configs: {"download_dir":null}, connection configs: {"access_config":"**********"}
2025-05-26 19:23:12,627 MainProcess INFO     created partition with configs: {"strategy":"hi_res","ocr_languages":null,"encoding":null,"additional_partition_args":{"split_pdf_page":true,"split_pdf_allow_failed":true,"split_pdf_concurrency_level":8},"skip_infer_table_types":null,"fields_include":["element_id","text","type","metadata","embeddings"],"flatten_metadata":false,"metadata_exclude":[],"element_exclude":[],"metadata_include":[],"partition_endpoint":"https://api.unstructuredapp.io/general/v0/general","partition_by_api":false,"api_timeout_ms":null,"api_key":"**********","hi_res_model_name":null,"raise_unsupported_filetype":false}
2

[DEBUG] get_connection connect_kwargs: {'access_config': Secret('**********'), 'schema': 'clickzetta_doc_kb', 'service': 'uat-api.clickzetta.com', 'username': 'qiliang', 'instance': 'jnsxwfyr', 'workspace': 'quick_start', 'vcluster': 'DEFAULT_AP', 'connector_type': 'clickzetta', 'password': 'Ql123456!', 'paramstyle': 'qmark'}


2025-05-26 19:23:23,318 MainProcess INFO     running local pipeline: indexer (LocalIndexer) -> download (LocalDownloader) -> partition (hi_res) -> chunk (by_title) -> embed (huggingface) -> upload_stage (ClickzettaUploadStager) -> upload (ClickzettaUploader) with configs: {"reprocess":false,"verbose":true,"tqdm":true,"work_dir":"/Users/liangmo/.cache/unstructured/ingest/pipeline","num_processes":8,"max_connections":null,"raise_on_error":false,"disable_parallelism":false,"preserve_downloads":false,"download_only":false,"re_download":false,"uncompress":false,"iter_delete":false,"delete_cache":false,"otel_endpoint":null,"status":{}}
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
2025-05-26 19:23:23,399 MainProcess IN

[DEBUG] get_connection connect_kwargs: {'access_config': Secret('**********'), 'schema': 'clickzetta_doc_kb', 'service': 'uat-api.clickzetta.com', 'username': 'qiliang', 'instance': 'jnsxwfyr', 'workspace': 'quick_start', 'vcluster': 'DEFAULT_AP', 'connector_type': 'clickzetta', 'password': 'Ql123456!', 'paramstyle': 'qmark'}
[DEBUG] get_connection connect_kwargs: {'access_config': Secret('**********'), 'schema': 'clickzetta_doc_kb', 'service': 'uat-api.clickzetta.com', 'username': 'qiliang', 'instance': 'jnsxwfyr', 'workspace': 'quick_start', 'vcluster': 'DEFAULT_AP', 'connector_type': 'clickzetta', 'password': 'Ql123456!', 'paramstyle': 'qmark'}
[DEBUG] get_connection connect_kwargs: {'access_config': Secret('**********'), 'schema': 'clickzetta_doc_kb', 'service': 'uat-api.clickzetta.com', 'username': 'qiliang', 'instance': 'jnsxwfyr', 'workspace': 'quick_start', 'vcluster': 'DEFAULT_AP', 'connector_type': 'clickzetta', 'password': 'Ql123456!', 'paramstyle': 'qmark'}
[DEBUG] get_conn

2025-05-26 19:23:46,372 SpawnPoolWorker-35 DEBUG    /Users/liangmo/.cache/unstructured/ingest/pipeline/indexer/424b07d8344c.json not detected as batch file data
/Users/liangmo/Documents/GitHub/unstructured-ingest-clickzetta/unstructured_ingest/processes/connectors/sql/clickzetta.py:312: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.replace({np.nan: None}, inplace=True)
2025-05-26 19:23:46,404 SpawnPoolWorker-40 DEBUG    /Users/liangmo/.cache/unstructured/ingest/pipeline/indexer/b1f58fa580de.json not detected as batch file data
/Users/liangmo/Documents/GitHub/unstructured-ingest-clickzetta/unstructured_ingest/processes/connectors/sql/clickzetta.py:312: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydat

...

[DEBUG] get_connection connect_kwargs: {'access_config': Secret('**********'), 'schema': 'clickzetta_doc_kb', 'service': 'uat-api.clickzetta.com', 'username': 'qiliang', 'instance': 'jnsxwfyr', 'workspace': 'quick_start', 'vcluster': 'DEFAULT_AP', 'connector_type': 'clickzetta', 'password': 'Ql123456!', 'paramstyle': 'qmark'}


Removed trailing semicolon and whitespace from query
2025-05-26 19:26:58,466 SpawnPoolWorker-35 DEBUG    upload finished in 1.326472s, attributes: file_id=d7a1438c847c
2025-05-26 19:26:58,467 SpawnPoolWorker-37 DEBUG    upload finished in 1.41915s, attributes: file_id=bfc7e681bef3
2025-05-26 19:26:58,467 SpawnPoolWorker-35 DEBUG    upload finished in 1.327219s, attributes: file_id=d7a1438c847c
upload:  99%|█████████▉| 1047/1056 [03:13<00:01,  5.00it/s]2025-05-26 19:26:58,467 SpawnPoolWorker-37 DEBUG    upload finished in 1.419832s, attributes: file_id=bfc7e681bef3
2025-05-26 19:26:58,470 SpawnPoolWorker-37 DEBUG    /Users/liangmo/.cache/unstructured/ingest/pipeline/indexer/93299252d6f6.json not detected as batch file data
2025-05-26 19:26:58,470 SpawnPoolWorker-35 DEBUG    /Users/liangmo/.cache/unstructured/ingest/pipeline/indexer/41117e10b408.json not detected as batch file data
/Users/liangmo/Documents/GitHub/unstructured-ingest-clickzetta/unstructured_ingest/processes/connectors/sql

[DEBUG] get_connection connect_kwargs: {'access_config': Secret('**********'), 'schema': 'clickzetta_doc_kb', 'service': 'uat-api.clickzetta.com', 'username': 'qiliang', 'instance': 'jnsxwfyr', 'workspace': 'quick_start', 'vcluster': 'DEFAULT_AP', 'connector_type': 'clickzetta', 'password': 'Ql123456!', 'paramstyle': 'qmark'}
[DEBUG] get_connection connect_kwargs: {'access_config': Secret('**********'), 'schema': 'clickzetta_doc_kb', 'service': 'uat-api.clickzetta.com', 'username': 'qiliang', 'instance': 'jnsxwfyr', 'workspace': 'quick_start', 'vcluster': 'DEFAULT_AP', 'connector_type': 'clickzetta', 'password': 'Ql123456!', 'paramstyle': 'qmark'}
[DEBUG] get_connection connect_kwargs: {'access_config': Secret('**********'), 'schema': 'clickzetta_doc_kb', 'service': 'uat-api.clickzetta.com', 'username': 'qiliang', 'instance': 'jnsxwfyr', 'workspace': 'quick_start', 'vcluster': 'DEFAULT_AP', 'connector_type': 'clickzetta', 'password': 'Ql123456!', 'paramstyle': 'qmark'}


2025-05-26 19:26:58,673 SpawnPoolWorker-40 DEBUG    upload finished in 1.385776s, attributes: file_id=d187f9625869
2025-05-26 19:26:58,674 SpawnPoolWorker-40 DEBUG    upload finished in 1.386669s, attributes: file_id=d187f9625869
2025-05-26 19:26:58,806 SpawnPoolWorker-36 DEBUG    upload finished in 1.526152s, attributes: file_id=8d4fa2b55aa2
2025-05-26 19:26:58,806 SpawnPoolWorker-36 DEBUG    upload finished in 1.52679s, attributes: file_id=8d4fa2b55aa2
upload: 100%|█████████▉| 1051/1056 [03:14<00:00,  7.18it/s]Removed trailing semicolon and whitespace from query
2025-05-26 19:26:59,004 SpawnPoolWorker-39 DEBUG    upload finished in 1.724137s, attributes: file_id=9eb85e469c3e
2025-05-26 19:26:59,005 SpawnPoolWorker-39 DEBUG    upload finished in 1.725491s, attributes: file_id=9eb85e469c3e
Removed trailing semicolon and whitespace from query
2025-05-26 19:26:59,365 SpawnPoolWorker-38 DEBUG    upload finished in 1.445125s, attributes: file_id=4bc82a50626e
2025-05-26 19:26:59,365 SpawnPo

PipelineError: Pipeline did not run successfully

In [ ]:
# pipeline = Pipeline.from_configs(

#     context=ProcessorConfig(
#         verbose=True,
#         tqdm=True,
#         num_processes=20,
#     ),

#     indexer_config=S3IndexerConfig(remote_url=os.getenv("AWS_S3_NAME"), recursive=True, file_glob="**/*.md" ),
#     downloader_config=S3DownloaderConfig(),
#     source_connection_config=S3ConnectionConfig(
#         access_config=S3AccessConfig(
#             key=os.getenv("AWS_KEY"),
#             secret=os.getenv("AWS_SECRET"))
#     ),

#     partitioner_config=PartitionerConfig(
#         partition_by_api=False,
#         api_key=os.getenv("UNSTRUCTURED_API_KEY"),
#         partition_endpoint=os.getenv("UNSTRUCTURED_URL"),
#         strategy="hi_res",
#         additional_partition_args={
#             "split_pdf_page": True,
#             "split_pdf_allow_failed": True,
#             "split_pdf_concurrency_level": 15
#         }
#     ),

#     chunker_config=ChunkerConfig(
#         chunking_strategy="by_title",
#         chunk_max_characters=chunk_max_characters,
#         chunk_overlap=chunk_overlap,
#         chunk_combine_text_under_n_chars=200,
#     ),

#     embedder_config=EmbedderConfig(
#         embedding_provider = embedding_provider,
#         embedding_model_name = embedding_model_name,
#     ),

#     destination_connection_config=ClickzettaConnectionConfig(
#         access_config=ClickzettaAccessConfig(password=_password),
#         username=_username,
#         service=_service,
#         instance=_instance,
#         workspace=_workspace,
#         schema=_schema,
#         vcluster=_vcluster,
#     ),
#     stager_config=ClickzettaUploadStagerConfig(),
#     uploader_config=ClickzettaUploaderConfig(table_name=raw_table_name, documents_original_source="https://yunqi.tech/documents"),
# )

# pipeline.run()

### Clean/Transformation RAW table and Insert into Silver table

In [15]:
# You could excute more SQLs to clean and transform data before insert into Silver table.、
excute_sql(conn, clean_transformation_data_sql)

[['OPERATION SUCCEED']]

### Retrieve relevant documents from Singdata Lakehouse


In [16]:
from sentence_transformers import SentenceTransformer


def get_embedding(query):
    model = SentenceTransformer(embedding_model_name)
    return model.encode(query, normalize_embeddings=True)

def retrieve_documents(conn, query: str, num_results: int = 10):

    embedding = get_embedding(query)
    embedding_list = embedding.tolist()
    embedding_json = json.dumps(embedding_list)

    with conn.cursor() as cur:

        stmt = f"""
            WITH 
            vector_embedding_result AS (
            SELECT
                "vector_embedding" as retrieve_method,
                record_locator,
                type,
                filename,
                text,
                orig_elements,
                cosine_distance(embeddings, cast({embedding_list} as vector({embeddings_dimensions}))) AS score
            FROM {silver_table_name}
            ORDER BY score ASC
            LIMIT {num_results} 
            )
            SELECT    *  FROM      vector_embedding_result
           
            ORDER by score ASC;
        """

        cur.execute(stmt)

        results = cur.fetchall()
        columns = [desc[0] for desc in cur.description]  # Get column names from cursor description
        df = pd.DataFrame(results, columns=columns)
    return df

In [17]:
query_text = "创建索引的语法是什么？"
retrieve_documents_df = retrieve_documents(conn, query_text)
retrieve_documents_df

retrieve_method                                     record_locator  \
0  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   
1  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   
2  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   
3  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   
4  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   
5  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   
6  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   
7  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   
8  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   
9  vector_embedding  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...   

               type                     filename  \
0  CompositeElement      build-inverted-index.md   
1  CompositeElement     create-inverted-index.md   
2  CompositeElement       create-vector-index.md   
3  CompositeElement       create-vector-index.md   
4  CompositeElement            inverted-index.md   
5  CompositeElement            inverted-index.md   
6  CompositeElement  CREATE-BLOOMFILTER-INDEX.md   
7  CompositeElement            create-synonym.md   
8  CompositeElement         show-create-table.md   
9  CompositeElement                    create.md   

                                                text  \
0  构建索引\n\n对存量数据添加索引。目前只支持向量索引和倒排索引。布隆过滤器不支持\n\n语...   
1  创建倒排索引\n\n具体介绍参考倒排索引介绍\n\n语法\n\nSQL CREATE TAB...   
2  创建向量索引\n\n语法\n\nSQL CREATE TABLE table_name( c...   
3  已有的表增加向量索引\n\n语法\n\nSQL CREATE VECTOR INDEX [I...   
4  案例\n\nSQL CREATE TABLE inverted_index_test( id...   
5  倒排索引\n\n【预览发布】本功能当前处于公开预览发布阶段。\n\n倒排索引原理介绍\n\n...   
6  创建BLOOMFILTER索引\n\n功能\n\n布隆过滤器（Bloom Filter）是一...   
7  功能\n\n创建同义词，同义词synonym是一个数据库对象，类似给对象起一个别名。支持为以...   
8  功能\n\nSHOW CREATE TABLE 命令用于获取指定表、物化视图或视图的创建语句...   
9  功能描述\n\n创建指定类型的对象\n\n语法\n\nCREATE <object_type...   

                                       orig_elements     score  
0  eJztWNtuGzcQ/ZXtvuQltnm/OE0fggRoiiC9xWiB2BB4GT...  0.273337  
1  eJztXGlvG0cS/SsEv9gBfPR9eLEfEluLFeDYXkveDWALRB...  0.294409  
2  eJztXOlv3DYW/1eI+bCwAcfD++gFdFNjG6BNuom7XaAODJ...  0.326366  
3  eJztmN1v2zYQwP8VQU8JkA9+f6TYQ9d5QIAi6RJ3KBAHLk...  0.331133  
4  eJztXWuTEzcW/Su9/jJQ4aH3lciyVUmYVNgiwMKwSRVQjh...  0.340637  
5  eJztXelvHDeW/1d69SkBkpj3YUwW8E68OwYcZzZWZrGIAo...  0.346242  
6  eJztW1lvG0cS/isEX5QAkdX3YSAPsSNjBchWYCvYAJJA9F...  0.355196  
7  eJztW1lv29gV/iuEXqYPSXz3xUEf3MQDGPDSOs4UaWIodz...  0.367206  
8  eJztW21TW7kV/it3/CVkFozeX9JpZ2jibZhJYAukmXbJ2J...  0.370698  
9  eJztmllvGzcQx7+KoJe+1DHvIygCKIrSCJAlwJLTpIkhkM...  0.375958

In [18]:
first_row__text = retrieve_documents_df.iloc[4]['text']
print(first_row__text)

案例

SQL CREATE TABLE inverted_index_test( id int, name string, INDEX id_index (id) INVERTED , INDEX name_index (name) INVERTED PROPERTIES('analyzer'='keyword','mode' = 'smart|max_word') );

已有的表增加倒排索引

语法

SQL CREATE INVERTED INDEX [IF NOT EXISTS] index_name ON TABLE [schema].table_name(col_name) [COMMENT 'comment'] PROPERTIES('analyzer'='english｜chinese|keyword｜unicode','mode' = 'smart|max_word')

INVERTED: 索引类型，倒排索引

index_name: 表名字，位于schema下，schema下索引名称不能重复

col_name：列名只支持单列

PROPERTIES：指定INDEX的参数，支持的属性目前支持指定分词。数值和日期类型则不需要指定properties，如果是字符串类型要求必须指定分词

说明

执行CREATE INDEX仅对新增数据有效，对已有数据进行索引请使用BUILD INDEX命令。

案例

```SQL CREATE TABLE inverted_index_test( id int, name string );

CREATE INVERTED INDEX id_index ON TABLE public.inverted_index_test(name) PROPERTIES('analyzer'='unicode') ```

使用倒排索引查询

构建索引

对存量数据添加倒排索引

语法

SQL -- 语法 1，默认给全表的存量数据加上倒排索引 BUILD INDEX index_name ON [schema].table_name; -- 语法 2，可指定partition，可指定一个或多个,支持=, !=, >, >=, <, <= BUILD INDEX index_name ON table_name WHERE

In [19]:
filename = retrieve_documents_df.iloc[0]['filename']
with conn.cursor() as cur:

        stmt = f"""
            WITH 
            results AS (
            SELECT
                record_locator,
                type,
                filename,
                text,
                orig_elements,
            FROM {silver_table_name}
            WHERE filename = "{filename}"
            )
            SELECT    *  FROM      results;
        """

        cur.execute(stmt)

        results = cur.fetchall()
        columns = [desc[0] for desc in cur.description]  # Get column names from cursor description
        df = pd.DataFrame(results, columns=columns)
df

record_locator              type  \
0  {"path": "/Users/liangmo/yunqidoc/cn_markdown_...  CompositeElement   

                  filename                                               text  \
0  build-inverted-index.md  构建索引\n\n对存量数据添加索引。目前只支持向量索引和倒排索引。布隆过滤器不支持\n\n语...   

                                       orig_elements  
0  eJztWNtuGzcQ/ZXtvuQltnm/OE0fggRoiiC9xWiB2BB4GT...

In [20]:
all_text = "".join(df["text"].astype(str).tolist())
print(all_text)

构建索引

对存量数据添加索引。目前只支持向量索引和倒排索引。布隆过滤器不支持

语法

SQL -- 语法 1，默认给全表的存量数据加上索引 BUILD INDEX index_name ON [schema].table_name; -- 语法 2，可指定partition，可指定一个或多个,支持=, !=, >, >=, <, <= BUILD INDEX index_name ON table_name WHERE partition_name1 = '1' and partition_name2 = '2';

index_name：指定要添加索引名称

支持指定分区构建：可以指定一个或者多个

说明

执行BULD INDEX是一个同步任务，执行过程会消耗计算资源。查看进度可以通过Job Profile查看。

当分区表数据量较大时，建议以分区为粒度依次创建索引。

案例

SQL BUILD INDEX bulkload_data_index ON public.bulkload_data ;


In [21]:
kb = "ClickZetta\云器\Singdata之间的关系:ClickZetta是云器、Singdata的技术品牌。云器是ClickZetta的中国商业公司，Singdata是ClickZetta的海外商业公司。所以在不区分商业和技术的时候，三者是等同的。另外云器经常也会用到Yunqi的汉语拼音名称。"
embedded_kb = get_embedding(kb)
embedded_kb = embedded_kb.tolist()
add_kb_sql = f"""
INSERT INTO quick_start.clickzetta_doc_kb.{silver_table_name} (
  id, type, record_id, element_id, filetype, last_modified, languages, text, embeddings, date_created, date_modified, date_processed
) VALUES (
  uuid(), 'UserInput', uuid(), uuid(), 'text', CURRENT_TIMESTAMP, '["zh-cn"]',
  '{kb}',
  CAST('{embedded_kb}' AS vector(float,{embeddings_dimensions})), CURRENT_TIMESTAMP, CURRENT_TIMESTAMP, CURRENT_TIMESTAMP
);
"""

In [ ]:
with conn.cursor() as cur:
        cur.execute(add_kb_sql)

: 